In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px

In [2]:
df = pd.read_csv('preprocessed_data.csv',index_col=0)
df_geo = pd.read_csv('preprocessed_geo.csv')
top10_kota = pd.read_csv('top10_kota.csv')
top10_provinsi = pd.read_csv('top10_provinsi.csv')

In [12]:
 def earthquake_month(df):
        #order = ['January', 'February', 'March', 'April', 'May', 'June',
        #        'July', 'August', 'September', 'October', 'November', 'December']
        vfunc = np.vectorize(lambda x: pd.to_datetime(str(x), format='%m').strftime('%B'))
        order = vfunc(np.sort(df['month'].unique()))
        group = df.groupby('month_name').agg({'magnitude':['count','mean'],'depth':'mean'})
        group.columns = group.columns.map(lambda x: ' '.join(x))
        sorted_group = group.loc[order]
        sorted_group.reset_index(inplace=True)
        month_fig = px.bar(data_frame=sorted_group.round(2),x='month_name',y='magnitude count',
                    title='Earthquake Frequency by Month',color_discrete_sequence=['rgb(178, 34, 34)'],
                    hover_data={'month_name':False,'magnitude count':True,'magnitude mean':True,'depth mean':True},hover_name='month_name')
        # add a line plot
        month_fig.add_trace(px.line(data_frame=sorted_group.round(2), x='month_name', y='magnitude count',
                            color_discrete_sequence=['#1f77b4']).update_traces(line=dict(width=3)).data[0])
        month_fig.update_layout(plot_bgcolor='rgba(0, 0, 0, 0)', paper_bgcolor='rgba(0, 0, 0, 0)')
        month_fig.update_xaxes(title_text="Count")
        month_fig.update_yaxes(title_text="Month")
        return month_fig

def earthquake_year(df):
    group = df.groupby('year').agg({'magnitude':['count','mean'],'depth':'mean'})
    group.columns = group.columns.map(lambda x: ' '.join(x))
    group.reset_index(inplace=True)
    # create the bar chart
    year_fig = px.bar(data_frame=group.round(2), x='year', y='magnitude count',
                title='Earthquake Frequency by Year',color_discrete_sequence=['rgb(178, 34, 34)'],
                hover_data={'year':False,'magnitude count':True,'magnitude mean':True,'depth mean':True}, hover_name='year')

    # add a line plot
    year_fig.add_trace(px.line(data_frame=group.round(2), x='year', y='magnitude count',
                        color_discrete_sequence=['#1f77b4']).update_traces(line=dict(width=3)).data[0])

    # update the layout
    year_fig.update_layout(title='Earthquake Frequency by Year',
                    xaxis_title='Year', yaxis_title='Magnitude Count',plot_bgcolor='rgba(0, 0, 0, 0)', paper_bgcolor='rgba(0, 0, 0, 0)')
    year_fig.update_yaxes(title_text="Count")
    return year_fig

def earthquake_class(df):
    def earthquake_classification(mag):
        if mag == "Micro":
            mag_class = 1
        elif mag == "Minor":
            mag_class = 2
        elif mag <= "Light":
            mag_class = 3
        elif mag <= "Moderate":
            mag_class = 4
        else:
            mag_class = 5
        return mag_class
    def earthquake_classification_reverse(mag):
        if mag == 1:
            mag_class = "Micro"
        elif mag == 2:
            mag_class = "Minor"
        elif mag == 3:
            mag_class = "Light"
        elif mag == 4:
            mag_class = "Moderate"
        else:
            mag_class = "Strong"
        return mag_class
    vfunc = np.vectorize(earthquake_classification)
    vfunc_reverse = np.vectorize(earthquake_classification_reverse)
    order =vfunc_reverse(np.sort(vfunc(df['class'].unique())))
    #order = ['Micro','Minor','Light','Moderate','Strong']
    group = df.groupby('class').agg({'magnitude':['count','mean'],'depth':'mean'})
    group.columns = group.columns.map(lambda x: ' '.join(x))
    #group.reset_index(inplace=True)
    sorted_group = group.loc[order]
    sorted_group.reset_index(inplace=True)
    class_fig = px.bar(data_frame=sorted_group.round(2),x='class',y='magnitude count',
                title='Earthquake Frequency by Class',color_discrete_sequence=['rgb(178, 34, 34)'],
                hover_data={'class':False,'magnitude count':True,'magnitude mean':True,'depth mean':True},hover_name='class')
    class_fig.update_layout(plot_bgcolor='rgba(0, 0, 0, 0)', paper_bgcolor='rgba(0, 0, 0, 0)')
    class_fig.update_yaxes(title_text="Count")

    return class_fig

def create_density_map(dataframe):
    # Define hover data
    hover_data = {
        'date': True, 'magnitude': True, 'provinsi': True,
        'longitude': False, 'latitude': False
    }

    # Create density map figure
    map_fig = px.density_mapbox(
        dataframe, lat='latitude', lon='longitude',
        z='magnitude', radius=2, center=dict(lat=-2.5, lon=118),
        zoom=3.8, hover_name='id',
        hover_data=hover_data, color_continuous_scale='Hot',
        mapbox_style='carto-darkmatter', template='plotly_dark'
    )

    # Update figure layout
    map_fig.update_layout(
        width=1000, height=575,
        margin=dict(r=1, t=1, l=1, b=1), plot_bgcolor='rgba(0, 0, 0, 0)', paper_bgcolor='rgba(0, 0, 0, 0)'
    )

    # Update colorbar location and orientation
    map_fig.update_coloraxes(
        showscale=True,
        colorbar=dict(
            len=0.3, yanchor='bottom', y=0,
            xanchor='center',
            thickness=10, title='Earthquake Magnitude',
            orientation='h', title_side="top")
    )

    return map_fig

def top10_provinsi_plot(data_plot):
    earthquake_provinsi = data_plot.groupby('provinsi')['id'].count()
    top10_provinsi = earthquake_provinsi.drop('Sea').sort_values(ascending=False).head(10)
    top10_provinsi = pd.DataFrame(top10_provinsi.reset_index())
    top10_provinsi.rename({'id':'count'},axis=1,inplace=True)
    provinsi_fig = px.bar(data_frame=top10_provinsi,y='provinsi',x='count',color_discrete_sequence=['rgb(178, 34, 34)'],
                title='Earthquake Frequency by Province',hover_data={'provinsi':False},hover_name='provinsi',orientation='h')
    provinsi_fig.update_layout(
        height=575, plot_bgcolor='rgba(0, 0, 0, 0)', paper_bgcolor='rgba(0, 0, 0, 0)'
    )
    provinsi_fig.update_yaxes(autorange='reversed')
    return provinsi_fig

def top10_kota_plot(data_plot):
    earthquake_kota = data_plot.groupby('id')['provinsi'].count()
    top10_kota = earthquake_kota.drop('Sea').sort_values(ascending=False).head(10)
    top10_kota = pd.DataFrame(top10_kota.reset_index())
    top10_kota.rename({'id':'kota','provinsi':'count'},axis=1,inplace=True)
    kota_fig = px.bar(data_frame=top10_kota,y='kota',x='count',color_discrete_sequence=['rgb(178, 34, 34)'],
                title='Earthquake Frequency by City',hover_data={'kota':False},hover_name='kota',orientation='h')
    kota_fig.update_layout(
        height=575, plot_bgcolor='rgba(0, 0, 0, 0)', paper_bgcolor='rgba(0, 0, 0, 0)'
    )
    kota_fig.update_yaxes(autorange='reversed')
    return kota_fig

def earthquake_line(df):
    df.index =pd.to_datetime(df.index)
    group = df.groupby(level=0).agg({'magnitude':['count','mean'],'depth':'mean'})
    group.columns = group.columns.map(lambda x: ' '.join(x))
    group.reset_index(inplace=True)

    # Create the basic line chart
    group['date'] = group['date'].dt.date
    date_buttons = [
    {'count': 14, 'label': "All", 'step': "year", 'stepmode': "todate"},
    {'count': 12, 'label': "YTD", 'step': "month", 'stepmode': "todate"},
    {'count': 6, 'label': "6M", 'step': "month", 'stepmode': "todate"}]

    fig = px.line(data_frame=group.round(2),x='date', y='magnitude count', 
                title="Earthquake Frequency",color_discrete_sequence=['rgb(178, 34, 34)'],
                hover_data={'date':False,'magnitude count':True,'magnitude mean':True,'depth mean':True},hover_name='date')
    fig.update_layout(plot_bgcolor='rgba(0, 0, 0, 0)', paper_bgcolor='rgba(0, 0, 0, 0)')
    fig.update_layout(
        {'xaxis':
        {'rangeselector': {'buttons': date_buttons, 'font': {'color': 'black'}}}})
    return fig

In [13]:
dff = df.copy()
dff_geo = df_geo.copy()

In [14]:
create_density_map(dff_geo)

In [6]:
class_fig = earthquake_class(dff)

In [7]:
earthquake_year(dff)

In [8]:
earthquake_month(dff)

In [9]:
 top10_provinsi_plot(dff_geo)

In [10]:
top10_kota_plot(dff_geo)

In [11]:
earthquake_line(dff)